## Assignment 2
### Collaborators: Aldrin Ilagan, Lindsey Rappaport, Yvanna Cardenas

In [4]:
# Import packages (same from Workbook 3)
import glob
import random
from typing import List
from collections import defaultdict

import numpy as np
from numpy.random import choice

import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader

from symusic import Score
from miditok import REMI, TokenizerConfig

/Users/lindseyrappaport/Desktop/CSE153-Assignment-2/.venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [5]:
random.seed(42)

### Symbolic,  unconditioned generation

In [6]:
# Parse data
file_path = './maestro-v3.0.0/'
test_files = []
# Set train files to years 2004-2011
train_files = glob.glob(file_path + '2004/*.midi')
# train_files += glob.glob(file_path + '2006/*.midi')
# train_files += glob.glob(file_path + '2008/*.midi')
# train_files += glob.glob(file_path + '2009/*.midi')       # including the rest makes training take 2 min / epoch (very slow!)
# train_files += glob.glob(file_path + '2011/*.midi')

# Set test files to years 2013-2018
test_files = glob.glob(file_path + '2013/*.midi')
# test_files += glob.glob(file_path + '2014/*.midi')
# test_files += glob.glob(file_path + '2015/*.midi')
# test_files += glob.glob(file_path + '2017/*.midi')
# test_files += glob.glob(file_path + '2018/*.midi')

print(len(train_files))
print(len(test_files))


132
127


In [7]:
# Build Markov chain from training data
from miditok import REMI
from miditoolkit import MidiFile
from collections import defaultdict, Counter
import glob

# Initialize REMI tokenizer
tokenizer = REMI()

# Get all training MIDI file paths from MAESTRO v3.0.0 (years 2004–2011)
train_files = glob.glob('./maestro-v3.0.0/**/**/*.midi', recursive=True)
train_files = [f for f in train_files if any(str(y) in f for y in range(2004, 2012))]

# Initialize transition counter: token -> next_token -> count
transitions = defaultdict(Counter)

# Iterate over MIDI files and count token transitions
for file in train_files:
    encodings = tokenizer.encode(file)  # returns list of Encoding objects
    for encoding in encodings:
        ids = encoding.ids
        for i in range(len(ids) - 1):
            transitions[ids[i]][ids[i + 1]] += 1

# Normalize transition counts into probabilities
markov_model = {
    k: {kk: vv / sum(v.values()) for kk, vv in v.items()}
    for k, v in transitions.items()
}

print(f"Built Markov model with {len(markov_model)} unique starting tokens.")


Built Markov model with 217 unique starting tokens.


In [8]:
def generate_markov_sequence(start_token, length=200):
    sequence = [start_token]
    for _ in range(length - 1):
        curr = sequence[-1]
        next_tokens = markov_model.get(curr, {})
        if not next_tokens:
            break
        next_token = random.choices(
            list(next_tokens.keys()), weights=list(next_tokens.values()), k=1
        )[0]
        sequence.append(next_token)
    return sequence

In [9]:
from miditok import TokSequence

# Generate a sequence using the Markov chain
start = random.choice(list(markov_model.keys()))
generated_ids = generate_markov_sequence(start)

# Wrap in a TokSequence and decode to ScoreTick
seq = TokSequence(ids=generated_ids)

try:
    score = tokenizer.decode([seq])  # returns symusic ScoreTick
    score.dump_midi("symbolic_unconditioned.mid")  # save directly to MIDI
    print("Saved symbolic_unconditioned.mid ✅")
except KeyError as e:
    print("❌ Decode failed due to invalid token ID:", e)

Saved symbolic_unconditioned.mid ✅


In [10]:
from miditok.pytorch_data import DatasetMIDI, DataCollator

tokenizer = REMI()  # using defaults parameters (constants.py)
train_dataset = DatasetMIDI(
    files_paths=train_files,
    tokenizer=tokenizer,
    max_seq_len=1024,
    bos_token_id=tokenizer["BOS_None"],
    eos_token_id=tokenizer["EOS_None"],
)
test_dataset = DatasetMIDI(
    files_paths=test_files,
    tokenizer=tokenizer,
    max_seq_len=1024,
    bos_token_id=tokenizer["BOS_None"],
    eos_token_id=tokenizer["EOS_None"],
)
collator = DataCollator(tokenizer.pad_token_id)
train_loader = DataLoader(train_dataset, batch_size=4, shuffle=True, collate_fn=collator)
test_loader = DataLoader(test_dataset, batch_size=4, shuffle=False, collate_fn=collator)


### Define RNN model (LSTM)

In [11]:
class MusicRNN(nn.Module):
    def __init__(self, vocab_size, embedding_dim, hidden_dim, num_layers):
        super(MusicRNN, self).__init__()
        self.embedding = nn.Embedding(vocab_size, embedding_dim)
        self.rnn = nn.LSTM(
            input_size=embedding_dim,
            hidden_size=hidden_dim,
            num_layers=num_layers,
            batch_first=True
        )
        self.fc = nn.Linear(hidden_dim, vocab_size)

    def forward(self, x, hidden=None):
        # x: (batch_size, seq_length)
        x = self.embedding(x)  # (batch_size, seq_length, embedding_dim)
        out, hidden = self.rnn(x, hidden)  # out: (batch_size, seq_length, hidden_dim)
        out = self.fc(out)  # (batch_size, seq_length, vocab_size)
        return out, hidden

### Define training function

In [12]:
def train(model, train_loader, val_loader, vocab_size, num_epochs=10, lr=0.001, device='mps'):
    model = model.to(device)
    criterion = nn.CrossEntropyLoss()
    optimizer = optim.Adam(model.parameters(), lr=lr)

    for epoch in range(num_epochs):
        # --------- Training ---------
        model.train()
        total_train_loss = 0

        for batch in train_loader:
            batch = batch['input_ids'].to(device)  # (batch_size, seq_length)

            inputs = batch[:, :-1]
            targets = batch[:, 1:]

            optimizer.zero_grad()
            outputs, _ = model(inputs)
            outputs = outputs.reshape(-1, vocab_size)
            targets = targets.reshape(-1)

            loss = criterion(outputs, targets)
            loss.backward()
            optimizer.step()

            total_train_loss += loss.item()

        avg_train_loss = total_train_loss / len(train_loader)

        # --------- Validation ---------
        model.eval()
        total_val_loss = 0
        with torch.no_grad():
            for batch in val_loader:
                batch = batch['input_ids'].to(device)

                inputs = batch[:, :-1]
                targets = batch[:, 1:]

                outputs, _ = model(inputs)
                outputs = outputs.reshape(-1, vocab_size)
                targets = targets.reshape(-1)

                loss = criterion(outputs, targets)
                total_val_loss += loss.item()

        avg_val_loss = total_val_loss / len(val_loader)

        print(f"Epoch {epoch+1}/{num_epochs} | Train Loss: {avg_train_loss:.4f} | Val Loss: {avg_val_loss:.4f}")


# Example usage
if __name__ == "__main__":
    vocab_size = tokenizer.vocab_size
    embedding_dim = 256
    hidden_dim = 512
    num_layers = 2

    model = MusicRNN(vocab_size, embedding_dim, hidden_dim, num_layers)
    train(model, train_loader, test_loader, vocab_size)

Epoch 1/10 | Train Loss: 3.1927 | Val Loss: 2.7151
Epoch 2/10 | Train Loss: 2.6084 | Val Loss: 2.5199
Epoch 3/10 | Train Loss: 2.4583 | Val Loss: 2.4200
Epoch 4/10 | Train Loss: 2.3330 | Val Loss: 2.3544
Epoch 5/10 | Train Loss: 2.2204 | Val Loss: 2.3189
Epoch 6/10 | Train Loss: 2.1072 | Val Loss: 2.3196
Epoch 7/10 | Train Loss: 1.9834 | Val Loss: 2.3290
Epoch 8/10 | Train Loss: 1.8546 | Val Loss: 2.3694
Epoch 9/10 | Train Loss: 1.7166 | Val Loss: 2.4305
Epoch 10/10 | Train Loss: 1.5783 | Val Loss: 2.5041


### Define sampling function

In [13]:
def sample(model, start_token, max_length=100, temperature=1.0, device='mps'):
    model = model.to(device)
    model.eval()

    generated = [start_token]
    input_token = torch.tensor([[start_token]], device=device)  # (1, 1)

    hidden = None

    for _ in range(max_length):
        output, hidden = model(input_token, hidden)  # output: (1, 1, vocab_size)
        output = output[:, -1, :]  # take the last output
        output = output / temperature  # adjust randomness

        probs = F.softmax(output, dim=-1)  # (1, vocab_size)
        next_token = torch.multinomial(probs, num_samples=1).item()
        generated.append(next_token)
        if next_token == 2 or next_token == 0: # reach end of sequence
          break

        input_token = torch.tensor([[next_token]], device=device)

    return generated

start_token = tokenizer.special_tokens_ids[1]
generated_sequence = sample(model, start_token, max_length=1024)

print("Generated token sequence:")
print(generated_sequence)

Generated token sequence:
[1, 4, 200, 54, 108, 163, 206, 30, 102, 133, 18, 102, 128, 212, 23, 97, 135, 216, 33, 102, 127, 220, 21, 103, 130, 4, 194, 33, 102, 132, 52, 105, 141, 195, 46, 101, 141, 33, 102, 125, 201, 21, 102, 134, 206, 33, 102, 136, 213, 54, 106, 133, 26, 102, 154, 50, 102, 154, 42, 101, 165, 4, 191, 53, 104, 135, 38, 99, 145, 197, 45, 102, 134, 42, 102, 129, 205, 45, 103, 125, 211, 31, 100, 142, 212, 37, 102, 135, 216, 55, 105, 125, 37, 102, 126, 45, 104, 125, 218, 53, 108, 127, 219, 50, 107, 127, 26, 105, 132, 4, 194, 26, 105, 127, 197, 42, 109, 133, 33, 102, 132, 202, 45, 105, 145, 203, 35, 101, 132, 38, 101, 133, 210, 41, 104, 133, 38, 101, 134, 4, 190, 37, 104, 128, 33, 102, 128, 202, 48, 105, 143, 29, 99, 136, 21, 98, 137, 33, 99, 136, 212, 26, 98, 129, 216, 38, 101, 128, 4, 190, 46, 103, 129, 25, 101, 127, 26, 101, 128, 194, 11, 97, 132, 199, 37, 101, 132, 26, 99, 132, 208, 38, 103, 132, 38, 101, 132, 212, 38, 99, 130, 4, 191, 42, 102, 143, 212, 21, 101, 145, 33, 

In [14]:
from midi2audio import FluidSynth # Import library
from IPython.display import Audio, display
fs = FluidSynth("FluidR3Mono_GM.sf3") # Initialize FluidSynth

In [15]:

output_score = tokenizer.tokens_to_midi([generated_sequence])
output_score.dump_midi(f"rnn.mid")
fs.midi_to_audio("rnn.mid", "rnn.wav")
display(Audio("rnn.wav"))

/var/folders/3y/s46f_xdj6ql6f_lxxcsd4wch0000gn/T/ipykernel_69599/72160659.py:1: UserWarning: miditok: The `tokens_to_midi` method had been renamed `decode`. It is now depreciated and will be removed in future updates.
  output_score = tokenizer.tokens_to_midi([generated_sequence])


FluidSynth runtime version 2.4.5
Copyright (C) 2000-2025 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of Creative Technology Ltd.

Rendering audio to file 'rnn.wav'..


### Symbolic, conditioned generation (harmonization)

In [16]:
# Define simple harmonization model with LSTM
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader

class HarmonizationDataset(Dataset):
    def __init__(self, file_paths, tokenizer):
        self.data = []
        for path in file_paths[:100]:  # limit to 100 for speed
            try:
                encodings = tokenizer.encode(path)
                ids = []
                for encoding in encodings:
                    ids.extend(encoding.ids)  # flatten all token segments
                for i in range(len(ids) - 16):
                    melody = ids[i:i+8]
                    chords = ids[i+8:i+16]
                    self.data.append((melody, chords))
            except Exception as e:
                print(f"Skipping file {path} due to error: {e}")

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        melody, chords = self.data[idx]
        return torch.tensor(melody), torch.tensor(chords)

class HarmonizationModel(nn.Module):
    def __init__(self, vocab_size, embed_dim=128, hidden_dim=256):
        super().__init__()
        self.embed = nn.Embedding(vocab_size, embed_dim)
        self.lstm = nn.LSTM(embed_dim, hidden_dim, batch_first=True)
        self.fc = nn.Linear(hidden_dim, vocab_size)

    def forward(self, x):
        x = self.embed(x)
        output, _ = self.lstm(x)
        logits = self.fc(output)
        return logits

In [17]:
# Create dataset and loader using train_files
dataset = HarmonizationDataset(train_files, tokenizer)
loader = DataLoader(dataset, batch_size=32, shuffle=True)

# Initialize model, loss, and optimizer
model = HarmonizationModel(tokenizer.vocab_size)
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)
loss_fn = nn.CrossEntropyLoss()

# Simple training loop
for epoch in range(7):
    model.train()
    train_losses = []

    for melody, chords in loader:
        preds = model(melody)
        loss = loss_fn(preds.view(-1, preds.shape[-1]), chords.view(-1))

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        train_losses.append(loss.item())

    avg_train_loss = sum(train_losses) / len(train_losses)
    print(f"Epoch {epoch+1}/10 | Train Loss: {avg_train_loss:.4f}")

Epoch 1/10 | Train Loss: 3.7499
Epoch 2/10 | Train Loss: 3.6950
Epoch 3/10 | Train Loss: 3.6715
Epoch 4/10 | Train Loss: 3.6553
Epoch 5/10 | Train Loss: 3.6434
Epoch 6/10 | Train Loss: 3.6348
Epoch 7/10 | Train Loss: 3.6279
Epoch 8/10 | Train Loss: 3.6224
Epoch 9/10 | Train Loss: 3.6180
Epoch 10/10 | Train Loss: 3.6143


In [18]:
# Select melody sample
melody, _ = dataset[0]

# Use trained model to predict chords
model.eval()
with torch.no_grad():
    preds = model(melody.unsqueeze(0))  
    pred_ids = preds.argmax(dim=-1).squeeze().tolist()  # Get predicted chord token IDs

In [19]:
from miditok import TokSequence

# Combine melody and predicted chords into one list of IDs
combined = melody.tolist() + pred_ids

# Wrap in a TokSequence
seq = TokSequence(ids=combined)

# Decode into a ScoreTick
score = tokenizer.decode([seq])  # returns ScoreTick

# Dump the ScoreTick to a .mid file
score.dump_midi("symbolic_conditioned.mid")
print("✅ Saved symbolic_conditioned.mid")

✅ Saved symbolic_conditioned.mid
